In [1]:
import sys
sys.path.append("../") # go to parent dir

%load_ext autoreload
%autoreload 2

In [107]:
from evrptw_gdp import EVRPTW

In [108]:
from utils.graph import draw_plain_graph, draw_graph
from utils.plot import plot_interactive_graph
from utils.utilities import create_optimal_edges, merge_variable_results
from utils.utilities import parse_csv_tables, calculate_distance_matrix, generate_index_mapping
from utils.utilities import trace_routes
import pandas as pd

In [116]:
instance = 'r104C5'
# instance = 'r105C5'
# instance = 'r201C10'
# instance = 'rc108C10'
# instance = 'c103C15'
# instance = 'c202C15'
# instance = 'rc103C15'
# instance = 'r105C15'
# instance = 'r202C15'
# instance = 'r102C15'

fpath = 'data/' + instance + '.csv'

In [113]:
m = EVRPTW()

In [117]:
duplicates = False
# xfrm_method = 'hull'
xfrm_method = 'bigm'
m.solve(fpath, duplicates, xfrm_method)

Using license file C:\gurobi910\win64\gurobi.lic
Academic license - for non-commercial use only - expires 2021-06-13
Read LP format model from file C:\Users\berwa\AppData\Local\Temp\tmpyjha5sdc.pyomo.lp
Reading time = 0.01 seconds
x277: 926 rows, 250 columns, 1566 nonzeros
Gurobi Optimizer version 9.1.0 build v9.1.0rc0 (win64)
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 926 rows, 250 columns and 1566 nonzeros
Model fingerprint: 0x2b7ad245
Model has 186 quadratic constraints
Variable types: 31 continuous, 219 integer (219 binary)
Coefficient statistics:
  Matrix range     [5e-01, 2e+02]
  QMatrix range    [1e+00, 1e+00]
  QLMatrix range   [5e-01, 3e+02]
  Objective range  [6e+00, 6e+01]
  Bounds range     [1e+00, 2e+02]
  RHS range        [1e+00, 2e+02]
  QRHS range       [6e+01, 2e+02]
Presolve removed 797 rows and 180 columns
Presolve time: 0.01s
Presolved: 129 rows, 70 columns, 666 nonzeros
Variable types: 22 continuous, 48 intege

In [26]:
var_list = ['xgamma', 'xw', 'xq', 'xa']
x = merge_variable_results(m, var_list)
x[x['state']>0].sort_values(['route', 'xw'])

route from   to  state          xw    xq         xa
0      1   D0  C71    1.0    0.000000  25.0  40.071031
2      1  C71   C1    1.0   46.000000  10.0  15.231546
3      1   C1   D1    1.0         NaN   NaN        NaN
1      2   D0   C5    1.0    0.000000  61.0  60.630000
4      2   C5  C99    1.0   16.403124  35.0  54.226876
6      2  C99  C87    1.0  166.000000  26.0  18.384776
5      2  C87   D1    1.0  194.384776   0.0   0.000000

In [28]:
x = getattr(m.instance, 'xgamma')
# keys, values = zip(*x.get_values().items())
x_val = x.extract_values()
active_arcs = [n for n in list(x_val.items()) if n[1] == 1.0]
active_arcs

[(('D0', 'C71'), 1.0),
 (('D0', 'C5'), 1.0),
 (('C71', 'C1'), 1.0),
 (('C1', 'D1'), 1.0),
 (('C5', 'C99'), 1.0),
 (('C87', 'D1'), 1.0),
 (('C99', 'C87'), 1.0)]

In [101]:
# m.instance.constraint_energy_customer.pprint()

In [99]:
m.instance.ArcOn.pprint()

ArcOn : Size=441, Index=ArcOn_index, Active=True
    ArcOn[C10,C10] : Active=True
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  None :     1 : False :  True : Binary

        1 Declarations: indicator_var
    ArcOn[C10,C13] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :   0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper                        : Active
                None :   0.0 : xa[C13] : xa[C10] - 15.811388300841896 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper : Active
                Non

    ArcOn[C18,S0] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                       : Active
                None :   0.0 : xa[S0] : xa[C18] - 35.35533905932738 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper  : Active
                None :   0.0 : xw[C18] : 1110.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper        : Active
                None :   0.0 : xq[S0] : xq[C18] - 20 :  False
            constraint_time_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body    

                Key  : Lower : Body    : Upper                       : Active
                None :   0.0 : xa[C10] : xa[C33] - 37.48332962798263 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper : Active
                None : 355.0 : xw[C33] : 437.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper        : Active
                None :   0.0 : xq[C10] : xq[C33] - 40 :  False
            constraint_time_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body                         : Upper   : Active
                None :   0.0 : xw[C33] + 127.48332962798263 : xw[C10] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body            : Upper : Active
                None :   1.0 : xgamma[C33,C10] :   1.0 :  False

        6 Declarations: indicator_var con

                Key  : Lower : Body            : Upper : Active
                None :   1.0 : xgamma[C40,C33] :   1.0 :  False

        6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_customer constraint_energy_customer
    ArcOn[C40,C35] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper                      : Active
                None :   0.0 : xa[C35] : xa[C40] - 30.4138126514911 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper : Active
                None : 143.0 : xw[C40] : 199.0 :  False
            constr

            constraint_time_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body                         : Upper   : Active
                None :   0.0 : xw[C50] + 111.21320343559643 : xw[C35] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body            : Upper : Active
                None :   1.0 : xgamma[C50,C35] :   1.0 :  False

        6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_customer constraint_energy_customer
    ArcOn[C50,C40] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper                  

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                       : Active
                None :   0.0 : xa[S7] : xa[C61] - 60.41522986797286 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper  : Active
                None : 980.0 : xw[C61] : 1064.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper        : Active
                None :   0.0 : xq[S7] : xq[C61] - 10 :  False
            constraint_time_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body                         : Upper  : Active
                None :   0.0 : xw[C61] + 150.41522986797287 : xw[S7] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body           : Upper : Active
   

    ArcOn[C98,C18] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper          : Active
                None :   0.0 : xa[C18] : xa[C98] - 43.0 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper  : Active
                None :   0.0 : xw[C98] : 1115.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper        : Active
                None :   0.0 : xq[C18] : xq[C98] - 20 :  False
            constraint_time_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body            : Upper   : A

                Key  : Lower : Body                                               : Upper   : Active
                None :   0.0 : xw[S0] + 35.05709628591621 + 3.47*(77.75 - xa[S0]) : xw[C59] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body           : Upper : Active
                None :   1.0 : xgamma[S0,C59] :   1.0 :  False

        6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_station constraint_energy_station
    ArcOn[S0,C61] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_station : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper            : Active
                None :   0.0 : 

        5 Constraint Declarations
            constraint_energy_station : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper             : Active
                None :   0.0 : xa[C19] : 35.70240791674272 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper  : Active
                None :   0.0 : xw[S3] : 1236.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper  : Active
                None :   0.0 : xq[C19] : xq[S3] :  False
            constraint_time_station : Size=1, Index=None, Active=False
                Key  : Lower : Body                                               : Upper   : Active
                None :   0.0 : xw[S3] + 42.04759208325728 + 3.47*(77.75 - xa[S3]) : xw[C19] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body           : Uppe

In [29]:
m.instance.ArcOn['C71', 'C1'].pprint()

{Member of ArcOn} : Size=81, Index=ArcOn_index, Active=True
    ArcOn[C71,C1] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :   1.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                        : Active
                None :   0.0 : xa[C1] : xa[C71] - 24.839484696748443 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper : Active
                None :   0.0 : xw[C71] : 180.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper        : Active
                None :   0.0 : xq[C1] : xq[C71] - 15 :  False
            constraint_time_customer : Size=1, Inde

In [100]:
m.instance.pprint()

16 Set Declarations
    ArcOff_index : Size=1, Index=None, Ordered=True
        Key  : Dimen : Domain  : Size : Members
        None :     2 : V0_*V1_ :  441 : {('D0', 'D1'), ('D0', 'S0'), ('D0', 'S3'), ('D0', 'S7'), ('D0', 'S13'), ('D0', 'S15'), ('D0', 'C61'), ('D0', 'C30'), ('D0', 'C98'), ('D0', 'C59'), ('D0', 'C35'), ('D0', 'C13'), ('D0', 'C10'), ('D0', 'C44'), ('D0', 'C50'), ('D0', 'C95'), ('D0', 'C18'), ('D0', 'C33'), ('D0', 'C85'), ('D0', 'C19'), ('D0', 'C40'), ('S0', 'D1'), ('S0', 'S0'), ('S0', 'S3'), ('S0', 'S7'), ('S0', 'S13'), ('S0', 'S15'), ('S0', 'C61'), ('S0', 'C30'), ('S0', 'C98'), ('S0', 'C59'), ('S0', 'C35'), ('S0', 'C13'), ('S0', 'C10'), ('S0', 'C44'), ('S0', 'C50'), ('S0', 'C95'), ('S0', 'C18'), ('S0', 'C33'), ('S0', 'C85'), ('S0', 'C19'), ('S0', 'C40'), ('S3', 'D1'), ('S3', 'S0'), ('S3', 'S3'), ('S3', 'S7'), ('S3', 'S13'), ('S3', 'S15'), ('S3', 'C61'), ('S3', 'C30'), ('S3', 'C98'), ('S3', 'C59'), ('S3', 'C35'), ('S3', 'C13'), ('S3', 'C10'), ('S3', 'C44'), ('S3', 'C50

        Key  : Active : Sense    : Expression
        None :   True : minimize : 36.235341863986875*xgamma[S3,D1] + 38.07886552931954*xgamma[S7,D1] + 24.08318915758459*xgamma[S13,D1] + 24.020824298928627*xgamma[S15,D1] + 22.360679774997898*xgamma[C61,D1] + 20.615528128088304*xgamma[C30,D1] + 30.805843601498726*xgamma[C98,D1] + 35.05709628591621*xgamma[C59,D1] + 38.07886552931954*xgamma[C35,D1] + 30.805843601498726*xgamma[C13,D1] + 16.76305461424021*xgamma[C10,D1] + 21.540659228538015*xgamma[C44,D1] + 22.80350850198276*xgamma[C50,D1] + 37.20215047547655*xgamma[C95,D1] + 35.35533905932738*xgamma[C18,D1] + 33.52610922848042*xgamma[C33,D1] + 29.732137494637012*xgamma[C85,D1] + 39.05124837953327*xgamma[C19,D1] + 20.615528128088304*xgamma[C40,D1] + 36.235341863986875*xgamma[S3,S0] + 38.07886552931954*xgamma[S7,S0] + 24.08318915758459*xgamma[S13,S0] + 24.020824298928627*xgamma[S15,S0] + 22.360679774997898*xgamma[C61,S0] + 20.615528128088304*xgamma[C30,S0] + 30.805843601498726*xgamma[C98,S0] +

        Key : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    : Upper : Active
        C10 :   0.0 : xgamma[C10,D1] + xgamma[C10,S0] + xgamma[C10,S3] + xgamma[C10,S7] + xgamma[C10,S13] + xgamma[C10,S15] + xgamma[C10,C61] + xgamma[C10,C30] + xgamma[C10,C98] + xgamma[C10,C59] + xgamma[C10,C35] + xgamma[C10,C13] + xgamma[C10,C44]

                Key            : Lower : Body                                                         : Upper : Active
                ('C10', 'C13') :   1.0 : ArcOn[C10,C13].indicator_var + ArcOff[C10,C13].indicator_var :   1.0 :   True
                ('C10', 'C18') :   1.0 : ArcOn[C10,C18].indicator_var + ArcOff[C10,C18].indicator_var :   1.0 :   True
                ('C10', 'C19') :   1.0 : ArcOn[C10,C19].indicator_var + ArcOff[C10,C19].indicator_var :   1.0 :   True
                ('C10', 'C30') :   1.0 : ArcOn[C10,C30].indicator_var + ArcOff[C10,C30].indicator_var :   1.0 :   True
                ('C10', 'C33') :   1.0 : ArcOn[C10,C33].indicator_var + ArcOff[C10,C33].indicator_var :   1.0 :   True
                ('C10', 'C35') :   1.0 : ArcOn[C10,C35].indicator_var + ArcOff[C10,C35].indicator_var :   1.0 :   True
                ('C10', 'C40') :   1.0 : ArcOn[C10,C40].indicator_var + ArcOff[C10,C40].indicator_var :   1.0 :   True
                ('C10', 'C44') :   1.0 : ArcOn[C

                            1 SetOf Declarations
                                ArcOn[C10,C85].indicator_var_index : Dimen=1, Size=1, Bounds=(None, None)
                                    Key  : Ordered : Members
                                    None :   False : UnindexedComponent_set

                            2 Declarations: ArcOn[C10,C85].indicator_var_index ArcOn[C10,C85].indicator_var

                    6 Declarations: localVarReferences ArcOn[C10,C85].constraint_xgamma ArcOn[C10,C85].constraint_node_time_window ArcOn[C10,C85].constraint_payload ArcOn[C10,C85].constraint_time_customer ArcOn[C10,C85].constraint_energy_customer
                _pyomo_gdp_bigm_reformulation.relaxedDisjuncts[23] : Active=True
                    2 Constraint Declarations
                        ArcOff[C10,C85].constraint_node_time_window : Size=2, Index=_pyomo_gdp_bigm_reformulation.lbub, Active=True
                            Key : Lower : Body                                              

...

            1 Var Declarations
                indicator_var : Size=1, Index=None
                    Key  : Lower : Value : Upper : Fixed : Stale : Domain
                    None :     0 :  -0.0 :     1 : False : False : Binary

            5 Constraint Declarations
                constraint_energy_customer : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper                        : Active
                    None :   0.0 : xa[S13] : xa[C85] - 52.839379254491625 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xw[C85] : 1116.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper        : Active
                    None :   0.0 : xq[S13] : xq[C85] - 30 :  False
                constraint_time_customer : Size=1, Index=None, Active=False
      


            6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_customer constraint_energy_customer
        ArcOn[C98,S0] : Active=False
            1 Var Declarations
                indicator_var : Size=1, Index=None
                    Key  : Lower : Value : Upper : Fixed : Stale : Domain
                    None :     0 :  -0.0 :     1 : False : False : Binary

            5 Constraint Declarations
                constraint_energy_customer : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper                        : Active
                    None :   0.0 : xa[S0] : xa[C98] - 30.805843601498726 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xw[C98] : 1115.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    K

            5 Constraint Declarations
                constraint_energy_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper             : Active
                    None :   0.0 : xa[C98] : 46.94415639850128 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper  : Active
                    None :   0.0 : xw[S0] : 1236.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xq[C98] : xq[S0] :  False
                constraint_time_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body                                                : Upper   : Active
                    None :   0.0 : xw[S0] + 30.805843601498726 + 3.47*(77.75 - xa[S0]) : xw[C98] :  False
                constraint_xgamma : Size=1, Index=None, Active=

                    Key  : Lower : Body    : Upper             : Active
                    None :   0.0 : xa[C19] : 35.70240791674272 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper  : Active
                    None :   0.0 : xw[S3] : 1236.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xq[C19] : xq[S3] :  False
                constraint_time_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body                                               : Upper   : Active
                    None :   0.0 : xw[S3] + 42.04759208325728 + 3.47*(77.75 - xa[S3]) : xw[C19] :  False
                constraint_xgamma : Size=1, Index=None, Active=False
                    Key  : Lower : Body           : Upper : Active
                    None :   1.0 : xgamma[S3

        Key            : Disjuncts                             : Active : XOR
        ('C10', 'C13') : ['ArcOn[C10,C13]', 'ArcOff[C10,C13]'] :  False : True
        ('C10', 'C18') : ['ArcOn[C10,C18]', 'ArcOff[C10,C18]'] :  False : True
        ('C10', 'C19') : ['ArcOn[C10,C19]', 'ArcOff[C10,C19]'] :  False : True
        ('C10', 'C30') : ['ArcOn[C10,C30]', 'ArcOff[C10,C30]'] :  False : True
        ('C10', 'C33') : ['ArcOn[C10,C33]', 'ArcOff[C10,C33]'] :  False : True
        ('C10', 'C35') : ['ArcOn[C10,C35]', 'ArcOff[C10,C35]'] :  False : True
        ('C10', 'C40') : ['ArcOn[C10,C40]', 'ArcOff[C10,C40]'] :  False : True
        ('C10', 'C44') : ['ArcOn[C10,C44]', 'ArcOff[C10,C44]'] :  False : True
        ('C10', 'C50') : ['ArcOn[C10,C50]', 'ArcOff[C10,C50]'] :  False : True
        ('C10', 'C59') : ['ArcOn[C10,C59]', 'ArcOff[C10,C59]'] :  False : True
        ('C10', 'C61') : ['ArcOn[C10,C61]', 'ArcOff[C10,C61]'] :  False : True
        ('C10', 'C85') : ['ArcOn[C10,C85]', 'ArcOff[C